In [4]:
from datasets import load_dataset
from transformers import BertTokenizer
dataset = load_dataset('tweet_eval','irony')
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')


In [2]:
dataset


DatasetDict({
    train: Dataset({
        features: ['text', 'label'],
        num_rows: 2862
    })
    test: Dataset({
        features: ['text', 'label'],
        num_rows: 784
    })
    validation: Dataset({
        features: ['text', 'label'],
        num_rows: 955
    })
})

In [3]:
tokenizer

BertTokenizer(name_or_path='bert-base-uncased', vocab_size=30522, model_max_length=512, is_fast=False, padding_side='right', truncation_side='right', special_tokens={'unk_token': '[UNK]', 'sep_token': '[SEP]', 'pad_token': '[PAD]', 'cls_token': '[CLS]', 'mask_token': '[MASK]'}, clean_up_tokenization_spaces=True),  added_tokens_decoder={
	0: AddedToken("[PAD]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	100: AddedToken("[UNK]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	101: AddedToken("[CLS]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	102: AddedToken("[SEP]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	103: AddedToken("[MASK]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
}

In [5]:
import re
import unidecode
def clean_keywords(keyword):
    cleaned = re.sub(r'%20', ' ', keyword)
    cleaned = unidecode.unidecode(keyword)
    cleaned = re.sub(r"[!\"#$%&()*+-./:;<=>?@[\]^_`{|}~\n -' ]"," ",keyword)
    return cleaned

In [6]:
def tokenize_function(example):
    return tokenizer(example["text"], padding="max_length", truncation=True)
tokenized_datasets = dataset.map(tokenize_function, batched=True)

In [7]:
tokenized_datasets["train"]

Dataset({
    features: ['text', 'label', 'input_ids', 'token_type_ids', 'attention_mask'],
    num_rows: 2862
})

In [8]:
tokenized_datasets

DatasetDict({
    train: Dataset({
        features: ['text', 'label', 'input_ids', 'token_type_ids', 'attention_mask'],
        num_rows: 2862
    })
    test: Dataset({
        features: ['text', 'label', 'input_ids', 'token_type_ids', 'attention_mask'],
        num_rows: 784
    })
    validation: Dataset({
        features: ['text', 'label', 'input_ids', 'token_type_ids', 'attention_mask'],
        num_rows: 955
    })
})

In [9]:
from transformers import  Trainer, TrainingArguments
from transformers import BertTokenizer, BertForSequenceClassification
import torch
import numpy as np
from sklearn.metrics import accuracy_score

tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")

model = BertForSequenceClassification.from_pretrained("bert-base-uncased",num_labels=2)

training_args = TrainingArguments(
output_dir="./results",
# Directory for saving outputs
learning_rate=5e-5,
# Learning rate for optimization
per_device_train_batch_size=16,
# Batch size for training
per_device_eval_batch_size=16,
# Batch size for evaluation
num_train_epochs=3,
# Number of training epochs
weight_decay=0.01,
# Weight decay for regularization
evaluation_strategy="epoch",
save_strategy = "no"
# Evaluation is done at the end of each epoch
)
train_dataset = tokenized_datasets["train"]
eval_dataset = tokenized_datasets["test"]
val_dataset = tokenized_datasets["validation"]
trainer = Trainer(
model=model,
args=training_args,
train_dataset=train_dataset,
eval_dataset=eval_dataset,
compute_metrics=lambda p: {"accuracy": accuracy_score(p.label_ids,
np.argmax(p.predictions,
axis=1))}
)

2024-03-08 23:23:27.199369: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-03-08 23:23:27.199414: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-03-08 23:23:27.201064: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-03-08 23:23:28.214132: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task 

In [10]:
model

BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12,

In [19]:
import os
os.environ["WANDB_DISABLED"] = "true"

In [20]:
eval_results = trainer.evaluate(val_dataset)
print(eval_results)

{'eval_loss': 0.701667845249176, 'eval_accuracy': 0.5214659685863874, 'eval_runtime': 32.9623, 'eval_samples_per_second': 28.972, 'eval_steps_per_second': 1.82}


In [28]:
from ray import tune
def ray_hp_space(trial):
    return {
        "learning_rate": tune.loguniform(1e-6, 1e-4),
        "per_device_train_batch_size": tune.choice([1,4 ,8 ]),
        "num_train_epochs": tune.choice([1,3,5]),

        "weight_decay": tune.loguniform(1e-4, 0.1)
    }

In [29]:
small_train_dataset = tokenized_datasets["train"].shard(index=1, num_shards=10) 
small_eval_dataset = tokenized_datasets["test"].shard(index=1, num_shards=10) 


In [30]:
num_labels = 2
from transformers import  Trainer, TrainingArguments
import numpy as np
from sklearn.metrics import accuracy_score
def model_init():
    return  BertForSequenceClassification.from_pretrained("bert-base-uncased",num_labels=num_labels)

In [25]:




num_labels = num_labels
trainer = Trainer(

    model_init= model_init,

    args=training_args,

    train_dataset=small_train_dataset,

    eval_dataset=small_eval_dataset,

    compute_metrics=lambda p: {"accuracy": accuracy_score(p.label_ids,
np.argmax(p.predictions,
axis=1))}

    

  
)

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [26]:
best_trial = trainer.hyperparameter_search(

    direction="maximize",

    backend="ray",

    hp_space=ray_hp_space,

    n_trials=30

)

/home/ai/anaconda3/lib/python3.11/subprocess.py:1883: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  self.pid = _fork_exec(
2024-03-07 06:52:07,135	INFO worker.py:1724 -- Started a local Ray instance.
2024-03-07 06:52:09,356	INFO tune.py:220 -- Initializing Ray automatically. For cluster usage or custom Ray initialization, call `ray.init(...)` before `tune.run(...)`.
2024-03-07 06:52:09,359	INFO tune.py:583 -- [output] This uses the legacy output and progress reporter, as Jupyter notebooks are not supported by the new engine, yet. For more information, please see https://github.com/ray-project/ray/issues/36949


== Status ==
Current time: 2024-03-07 06:52:09 (running for 00:00:00.21)
Using FIFO scheduling algorithm.
Logical resource usage: 0/12 CPUs, 0/1 GPUs (0.0/1.0 accelerator_type:G)
Result logdir: /home/ai/ray_results/_objective_2024-03-07_06-52-09
Number of trials: 16/30 (16 PENDING)
+------------------------+----------+-------+-----------------+--------------------+------------------------+----------------+
| Trial name             | status   | loc   |   learning_rate |   num_train_epochs |   per_device_train_bat |   weight_decay |
|                        |          |       |                 |                    |                ch_size |                |
|------------------------+----------+-------+-----------------+--------------------+------------------------+----------------|
| _objective_e1bbd_00000 | PENDING  |       |     5.61152e-06 |                  5 |                      1 |    0.015703    |
| _objective_e1bbd_00001 | PENDING  |       |     1.57513e-05 |                  3

(_objective pid=85040) 2024-03-07 06:52:15.492176: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
(_objective pid=85040) 2024-03-07 06:52:15.492224: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
(_objective pid=85040) 2024-03-07 06:52:15.493516: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
(_objective pid=85040) 2024-03-07 06:52:16.736103: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
(_objective pid=85040) Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newl

== Status ==
Current time: 2024-03-07 06:52:19 (running for 00:00:10.25)
Using FIFO scheduling algorithm.
Logical resource usage: 1.0/12 CPUs, 1.0/1 GPUs (0.0/1.0 accelerator_type:G)
Result logdir: /home/ai/ray_results/_objective_2024-03-07_06-52-09
Number of trials: 17/30 (16 PENDING, 1 RUNNING)
+------------------------+----------+------------------+-----------------+--------------------+------------------------+----------------+
| Trial name             | status   | loc              |   learning_rate |   num_train_epochs |   per_device_train_bat |   weight_decay |
|                        |          |                  |                 |                    |                ch_size |                |
|------------------------+----------+------------------+-----------------+--------------------+------------------------+----------------|
| _objective_e1bbd_00000 | RUNNING  | 172.19.0.1:85040 |     5.61152e-06 |                  5 |                      1 |    0.015703    |
| _objective

  2%|▏         | 33/1435 [00:04<03:18,  7.08it/s]


...

== Status ==
Current time: 2024-03-07 07:38:14 (running for 00:46:05.35)
Using FIFO scheduling algorithm.
Logical resource usage: 1.0/12 CPUs, 1.0/1 GPUs (0.0/1.0 accelerator_type:G)
Result logdir: /home/ai/ray_results/_objective_2024-03-07_06-52-09
Number of trials: 30/30 (9 ERROR, 1 RUNNING, 20 TERMINATED)
+------------------------+------------+------------------+-----------------+--------------------+------------------------+----------------+-------------+
| Trial name             | status     | loc              |   learning_rate |   num_train_epochs |   per_device_train_bat |   weight_decay |   objective |
|                        |            |                  |                 |                    |                ch_size |                |             |
|------------------------+------------+------------------+-----------------+--------------------+------------------------+----------------+-------------|
| _objective_e1bbd_00029 | RUNNING    | 172.19.0.1:94982 |     1.32603e-05

100%|██████████| 108/108 [01:22<00:00,  1.46it/s]
(_objective pid=94982) 
  0%|          | 0/5 [00:00<?, ?it/s]
(_objective pid=94982) 
 40%|████      | 2/5 [00:00<00:00,  3.83it/s]
(_objective pid=94982) 
 60%|██████    | 3/5 [00:01<00:00,  2.68it/s]
(_objective pid=94982) 
 80%|████████  | 4/5 [00:01<00:00,  2.32it/s]


== Status ==
Current time: 2024-03-07 07:38:18 (running for 00:46:09.56)
Using FIFO scheduling algorithm.
Logical resource usage: 1.0/12 CPUs, 1.0/1 GPUs (0.0/1.0 accelerator_type:G)
Result logdir: /home/ai/ray_results/_objective_2024-03-07_06-52-09
Number of trials: 30/30 (9 ERROR, 21 TERMINATED)
+------------------------+------------+------------------+-----------------+--------------------+------------------------+----------------+-------------+
| Trial name             | status     | loc              |   learning_rate |   num_train_epochs |   per_device_train_bat |   weight_decay |   objective |
|                        |            |                  |                 |                    |                ch_size |                |             |
|------------------------+------------+------------------+-----------------+--------------------+------------------------+----------------+-------------|
| _objective_e1bbd_00000 | TERMINATED | 172.19.0.1:85040 |     5.61152e-06 |         

(_objective pid=94982) 
                                                 
100%|██████████| 108/108 [01:24<00:00,  1.28it/s]


TuneError: ('Trials did not complete', [_objective_e1bbd_00002, _objective_e1bbd_00005, _objective_e1bbd_00007, _objective_e1bbd_00014, _objective_e1bbd_00015, _objective_e1bbd_00016, _objective_e1bbd_00020, _objective_e1bbd_00022, _objective_e1bbd_00025])

In [41]:
best_trial

{'learning_rate': 5.61151641533451e-06,
 'num_train_epochs': 5,
 'per_device_train_batch_size': 1,
 'weight_decay': 0.015702970884055385}

In [12]:

train_dataset = tokenized_datasets["train"]
eval_dataset = tokenized_datasets["test"]
val_dataset = tokenized_datasets["validation"]
trainer = Trainer(

model=model,
args=training_args,
train_dataset=train_dataset,
eval_dataset=eval_dataset,
compute_metrics=lambda p: {"accuracy": accuracy_score(p.label_ids,
np.argmax(p.predictions,
axis=1))}
)

In [43]:
for n, v in best_trial.hyperparameters.items():
    setattr(trainer.args, n, v)



In [44]:
trainer.args

TrainingArguments(
_n_gpu=1,
accelerator_config={'split_batches': False, 'dispatch_batches': None, 'even_batches': True, 'use_seedable_sampler': True},
adafactor=False,
adam_beta1=0.9,
adam_beta2=0.999,
adam_epsilon=1e-08,
auto_find_batch_size=False,
bf16=False,
bf16_full_eval=False,
data_seed=None,
dataloader_drop_last=False,
dataloader_num_workers=0,
dataloader_persistent_workers=False,
dataloader_pin_memory=True,
dataloader_prefetch_factor=None,
ddp_backend=None,
ddp_broadcast_buffers=None,
ddp_bucket_cap_mb=None,
ddp_find_unused_parameters=None,
ddp_timeout=1800,
debug=[],
deepspeed=None,
disable_tqdm=False,
dispatch_batches=None,
do_eval=True,
do_predict=False,
do_train=False,
eval_accumulation_steps=None,
eval_delay=0,
eval_steps=None,
evaluation_strategy=IntervalStrategy.EPOCH,
fp16=False,
fp16_backend=auto,
fp16_full_eval=False,
fp16_opt_level=O1,
fsdp=[],
fsdp_config={'min_num_params': 0, 'xla': False, 'xla_fsdp_v2': False, 'xla_fsdp_grad_ckpt': False},
fsdp_min_num_params=0,


In [14]:
trainer.train()

TrainOutput(global_step=14310, training_loss=0.7681977939139205, metrics={'train_runtime': 2031.2352, 'train_samples_per_second': 7.045, 'train_steps_per_second': 7.045, 'total_flos': 3765119202201600.0, 'train_loss': 0.7681977939139205, 'epoch': 5.0})

In [15]:
trainer.save_model('/home/ai/Downloads/results/last-bert-tweet')

In [16]:
predictions = trainer.evaluate(train_dataset)
print(predictions)

{'eval_loss': 0.24053911864757538, 'eval_accuracy': 0.960167714884696, 'eval_runtime': 96.6925, 'eval_samples_per_second': 29.599, 'eval_steps_per_second': 1.851, 'epoch': 5.0}


In [17]:
predictions = trainer.evaluate(eval_dataset)
print(predictions)

{'eval_loss': 2.0535099506378174, 'eval_accuracy': 0.6938775510204082, 'eval_runtime': 26.5115, 'eval_samples_per_second': 29.572, 'eval_steps_per_second': 1.848, 'epoch': 5.0}


In [18]:
predictions = trainer.evaluate(val_dataset)
print(predictions)

{'eval_loss': 1.9022417068481445, 'eval_accuracy': 0.7078534031413612, 'eval_runtime': 32.2777, 'eval_samples_per_second': 29.587, 'eval_steps_per_second': 1.859, 'epoch': 5.0}


In [19]:
predictions = trainer.predict(val_dataset)

In [20]:
predictions.predictions

array([[ 4.1072445, -3.3658538],
       [ 4.0091457, -3.262541 ],
       [-4.1539326,  4.036301 ],
       ...,
       [-4.030704 ,  3.8833497],
       [-3.8136315,  3.5384998],
       [ 4.2377563, -3.5568213]], dtype=float32)

In [21]:
import torch 
predictions.predictions
pre = torch.argmax(torch.tensor(predictions.predictions), dim=1)

In [22]:
true_labels = val_dataset['label']
true_labels

[1,
 0,
 1,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 1,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 1,
 0,
 0,
 0,
 1,
 1,
 1,
 1,
 1,
 0,
 0,
 1,
 0,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 0,
 0,
 1,
 0,
 0,
 1,
 1,
 1,
 1,
 0,
 1,
 0,
 0,
 1,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 0,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 1,
 1,
 0,
 1,
 0,
 1,
 0,
 0,
 1,
 1,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 1,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 1,
 0,
 0,
 1,


In [23]:

from sklearn.metrics import confusion_matrix
# Generate predictions, then create and print the confusion matrix
confusion_mat = confusion_matrix(true_labels, pre)
print(confusion_mat)

[[331 168]
 [111 345]]


In [24]:
predictions = trainer.predict(train_dataset)

In [25]:
predictions.predictions

array([[-3.766546 ,  3.6186543],
       [ 4.1580086, -3.4007418],
       [-4.074904 ,  3.9620261],
       ...,
       [ 4.080381 , -3.319614 ],
       [ 3.5725195, -2.8768601],
       [-4.2885985,  4.212216 ]], dtype=float32)

In [26]:
import torch 
predictions.predictions
pre = torch.argmax(torch.tensor(predictions.predictions), dim=1)
pre

tensor([1, 0, 1,  ..., 0, 0, 1])

In [27]:
true_labels = train_dataset['label']
true_labels

[1,
 0,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 0,
 0,
 1,
 1,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 0,
 1,
 0,
 1,
 0,
 0,
 1,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 1,
 1,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 0,
 1,
 1,
 0,
 0,
 0,
 1,
 1,
 1,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 0,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 0,
 1,
 0,
 0,
 1,
 1,
 0,
 0,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 1,
 1,
 1,
 0,
 0,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 0,
 1,
 0,
 0,
 0,


In [28]:

from sklearn.metrics import confusion_matrix
# Generate predictions, then create and print the confusion matrix
confusion_mat = confusion_matrix(true_labels, pre)
print(confusion_mat)

[[1362   55]
 [  59 1386]]


In [48]:
import random

num_examples = 10
picks = []
lable = []
input = []
prediction = [] 
for i in range(num_examples):
        pick = random.randint(0, len(dataset['validation'])-1)
        while pick in picks:
            pick = random.randint(0, len(dataset)-1)
        picks.append(pick)
        input.append(dataset['validation'][picks[i]]['text'])
        #input_token = tokenizer(dataset['validation'][picks[i]]['text'])
        lable.append(dataset['validation'][picks[i]]['label'])
        encoded_input = tokenizer(dataset['validation'][pick]['text'],return_tensors='pt').to(model.device)
        prediction.append(torch.argmax(trainer.model.forward(**encoded_input).logits, dim=1)[0].cpu().item())
    
    
    


In [49]:
print(input)
print(lable,"lable")
print(prediction,"prediction")



["I bet I'm the first to use that one", 'Chenua Achebe - when things fall apart', '@user @user the upper deck definitely seemed like Philly South.', '@user COD AW SERVERS #OFFLINE', 'My year is ending perfectly😂', "I don't know why it's so fun, but it is. cx I could probably think and find out, but yeah. No. xD", 'Thanks for the AWESOME support on our #instagram page. Much appreciated. #women #motivation #rolemode', 'Now i officially look single. Ha the', 'Porygon2 #are  found in the www.monstermmorpg. com #wild. bulbiest follow @user #working', '@user @user @user @user the Jets have pick 6 in the 2015 draft the irony blows my mind!  #NFLDraft']
[1, 0, 0, 0, 1, 0, 0, 1, 0, 1] lable
[1, 0, 1, 0, 0, 0, 0, 1, 0, 0] prediction
